# Chaos Control in Dynamical Systems

*Cem Özen*, January 2018

Chaotic attractors are made of a skeleton consisting of an infinite number of unstable periodic orbits.
A phase space point travelling along a trajectory in the phase space of the dynamical system spends only
short periods of time in these orbits. The purpose of chaos control is to stabilize a previously
chosen unstable periodic orbit by means of applying a small perturbation to
the system. This perturbation settles the dynamics onto a chosen periodic orbit. Control of chaos in this way opens up an interesting array of possibilities for numerous applications in magneto-mechanical systems, fluid dynamics, chemical reactions, and biological systems to name a few. 

<img src="./animations/duffing_chaos_control.gif" width="550"> <br><br>The animation above shows an application of the Pyragas method as a method of chaos control in the chaotic Duffing oscillator case (for the actual simulation, see below).

In [1]:
import numpy as np
from pylab import *
import scipy.interpolate
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib.colors import cnames
from matplotlib import animation, rc
from IPython.display import HTML
from time import time
from IPython.display import display, Math, Latex
%matplotlib inline

## The Pyragas Method

One of the most well-known methods of chaos control is the Pyragas (1992) method, which is also known as the delayed feedback control method. In this approach,  unstable periodic orbits are stabilized by applying small time continuous control to a parameter of the dynamical system of interest while it evolves in continuous time. Main advantages of this method are its easiness of implementation, and effectiveness for the less unstable periodic orbits

Consider a system evolving in a continuous time, described by variables $\boldsymbol{x} = \{x_1, x_2, \ldots, x_d\} \in \mathbb{R}^d$:<br>

$$\frac{d\boldsymbol{x}}{dt}  =  \boldsymbol{f}(\boldsymbol{x};p),  $$ <br>
where $p$ is an externally controllable parameter, which is zero
in the absence of external perturbations. It is also assumed that the behavior of the dynamical system when $p=0$ chaotic. Let $s(t)$ be a scalar observable of the system given by some function of the state of
the system $s(t) = \mu(\boldsymbol{x}(t))$.

The Pyragas method, then, stabilizes an unstable, periodic orbit $\boldsymbol{x}_p(t) = \boldsymbol{x}_p(t+\tau) $ by applying a perturbation of strength $C$ to modify the control parameter $p$ according to

$$ p(t) = C(s(t-\tau) - s(t))$$ 

where $s(t-\tau)$ is the signal measured with a time delay equal to $\tau$, hence the name *delayed feedback control*.

If $\tau$ is the period of an unstable periodic orbit embedded in the chaotic attractor---with no additional information on this orbit being necessary, by means of a proper
choice of the value of $C$, the unstable periodic orbit with period $\tau$ may be stabilized.

## An Application of the Pyragas Method

As an application of the Pyragas method, we will use the Duffing oscillator, which describes the motion of a damped oscillator in a double-well potential under the action of a harmonic force:

$$\frac{d^2x}{dt^2} + \gamma\frac{dx}{dt}-\frac{1}{2}x(1-x^2)=A \sin(t)$$.

The Duffing oscillator exhibits chaotic dynamics for the choice of the parameter values of $\gamma = 0.10$ and $A = 0.24$. We can describe the Duffing oscillator as a 3-D autonomous dynamical system as

$$
\begin{eqnarray}
\frac{dx}{dt} & = & y, \\
\frac{dy}{dt} & = & -\gamma y + \frac{1}{2}(x-x^3) + A \sin(z) + C(y(t-\tau) - y(t)), \\
\frac{dz}{dt} & = & 1,
\end{eqnarray}
$$

where the term $C(y(t-\tau) - y(t))$ represents the delayed feedback with perturbation strength $C$.

In [2]:
class duffing:
    def __init__(self, gamma=0.10, A=0.24):
        self.gamma = gamma
        self.A     = A

    def dx_dt(self, X, t):
        x, y, z     = X
        return np.array([y, -self.gamma*y + 0.5*(x-x**3) + self.A*np.sin(z), 1.])
    
    def delayed_dx_dt(self, X, t, X_delayed, C, t_on, t_off):
        """ here we utilize Pyragas method, by applying a perturbation (with strength C)
        during  t_on < t < t_off."""
        x, y, z     = X
        xd, yd, zd  = X_delayed
        if (t < t_on) or ( t > t_off): C = 0.0
        return self.dx_dt(X, t) + np.array([0., C*(yd-y), 0.])

Since the Pyragas method involves a delayed feedback, ODE integrators in `scipy.integrate` will not be applicable. For this reason, we need a solution method that can handle delay terms in the differential equations. We provide an implementation that utilizes a 4th order Runge-Kutta step:

In [3]:
class ODESolver:
    def __init__(self, f, dt, tau=None, params=[]):
        """ f is function in the form f=f(x,t). If tau and params given, then f=f(x,t,x_past,*params)
            where x_past is x=x(t-tau) where tau is the time delay.
            Cem Ozen, 2017    
        """
        self.f         = f       # dx/dt = f(x, t), if tau and params given f(x,t,x_past,*params)
        self.dt        = dt      # integration dt
        self.tau       = tau     # time delay, parameter for f 
        self.params    = params  # list of other parameters needed for the delayed system

    def advance(self):
        """Advance solution one time step"""
        raise NotImplementedError

    def set_initial_condition(self, g, t0=0.):
        """ g(t) is an expression for state vector for t<t0"""
        self.g = g
        self.u = []   # u[k] is solution at time t[k]
        self.t = []   # time levels in the solution process
        self.u.append(self.g(t0))
        self.t.append(t0)
        self.k = 0    # time level counter 

    def solve(self, T, terminate=None):
        """ Advance solution from t = t0 to t <= T, steps of dt
        as long as terminate(u, t, k) is False. 
        terminate(u, t, k) is a user-given function returning True or False.
        By default, a terminate function which always returns False is used """
        if terminate is None:
            terminate = lambda u, t, k: False
        self.k = 0
        t_present  = 0
        while t_present <= T and not terminate(self.u, self.t, self.k):
            t_present     = self.t[-1] + self.dt    # t builds up from t0 value in increments of dt
            if self.tau is not None:           # relevant if we solve delay ODEs
                t_past = t_present - self.tau    # time in past as present time - delay
                # below statement can cause error if not at least two members present in self.t and self.u
                # we construct an interpolator so that when we are given a certain time in the past
                # we can extract the state vector from the history of state vectors, which is discrete.
                try:
                    arr1 = np.array(self.t)
                    arr2 = np.array(self.u)
                    itrplt = scipy.interpolate.interp1d(arr1, arr2.T, kind='linear',
                                                        fill_value=np.array(self.u)[-1], bounds_error=False)
                    # interpolated value of the state vector at the time in the past.
                    self.u_past = self.g(t_past) if (t_past<=self.t[0]) else itrplt(t_past)  
                except ValueError:
                    print("At iteration k={:4d} (time t={:.4f}):".format(self.k+1, t_present))
                    print("linear interpolation for t_past={:.4f} requires at least two entries.".format(t_past))
                    self.u_past = self.g(t_past) 
                    #print("practically, I set the value of u_past to g({:.4f})={:.4f}".format(t_past,self.u_past))
                    
            u_present = self.advance()
            self.u.append(u_present)            
            self.t.append(t_present)
            self.k += 1
        return np.array(self.u), np.array(self.t)

class RungeKutta4(ODESolver):
    def advance(self):
        u, dt, f, k, t, tau, params = self.u, self.dt, self.f, self.k, self.t[-1], self.tau, self.params
        args = []
        if self.tau is not None:      # if we set explicit delay tau, then we will need to pass x(t-tau) 
            args = [self.u_past, *params]
        else:                         # we do not deal with explicit delay, hence x(t-tau) is irrelevant
            args = [*params]
        dt2 = dt/2.0
        k1  = dt * f(u[k], t, *args)
        k2 =  dt * f(u[k] + 0.5*k1, t + dt2, *args)
        k3 =  dt * f(u[k] + 0.5*k2, t + dt2, *args)
        k4 =  dt * f(u[k] + k3, t + dt, *args)
        unew = u[k] + (1./6.)*(k1 + 2*k2 + 2*k3 + k4)
        return unew


Now we can integrate the differential equations with the delayed feedback perturbation in.

Below I chose two orbits with randomly chosen initial points. You can change the number of trajectories, perturbation strength $C$, the delay parameter $\tau$, as well as the interval in which the perturbation is applied. 

Feel free to experiment, and enjoy!

In [8]:
tau   = 7.0  #2*np.pi + 0.17   # time-delay 
C     = 0.36             # strength of perturbation
t_on, t_off  = 20., 120  # time interval in which control perturbation is on
tstart, tstop = 0., 200. # simulation time  
dt = 0.2                 # integration time step


df   = duffing(gamma=0.10, A=0.24)
df_derivatives   = df.delayed_dx_dt
df_solver        = RungeKutta4(df_derivatives, dt, tau, [C, t_on, t_off])

N_trajectories = 2    # number of trajectories

# Choose random starting points, uniformly distributed
np.random.seed(1)
x0 = -1. + 2 * np.random.random((N_trajectories, 3))
 

x_t = []                     # to store all trajectories
for i in range(N_trajectories):
    g = lambda t: x0[i,:]    #  x=g(t) is the solution for t<=tstart
    df_solver.set_initial_condition(g, tstart)
    x, t = df_solver.solve(tstop)
    x_t.append(x)
x_t = np.asarray(x_t)

"""
fig = plt.figure(figsize = (8,5))
ax3 = fig.add_axes([0, 0, 1, 1], projection = '3d')  # x,y, width, height (all relative to 1)
x, y, z = x_t[0].T
#ax3.plot(x[:,0], x[:,1], x[:,2], 'k-', lw=1.0)
ax3.plot(x, y, z, 'k-', lw=1.0)
"""
# set up figure and axes
fig = plt.figure()
ax = fig.add_axes([0, 0, 1, 1], projection='3d')  # x,y, width, height (all relative to 1)
ax.axis('on')

# choose a different color for each trajectory
colors = plt.cm.jet_r(np.linspace(0, 1, N_trajectories))

# set up lines and points
lines = [ax.plot([], [], [], '-', c=c)[0] for c in colors]
pts = [ax.plot([], [], [], 'o', c=c)[0] for c in colors]

# set axes limits
ax.set_xlim((-2, 2))
ax.set_ylim((-2, 2))
ax.set_zlim((0, 150))

# set axis labels
ax.set_xlabel("x")
ax.set_ylabel("y")
ax.set_zlabel("z")

# set point-of-view
ax.view_init(30, 0)  # altitude and azimuth in degrees

# initialization function for the background of each frame
def init():
    for line, pt in zip(lines, pts):
        line.set_data([], [])
        line.set_3d_properties([])

        pt.set_data([], [])
        pt.set_3d_properties([])
    return lines + pts

# animation function.  This will be called sequentially with the frame number
def animate(i):
    # we'll step two time-steps per frame.  This leads to nice results.
    i = (6 * i) % x_t.shape[1]

    for line, pt, xi in zip(lines, pts, x_t):
        x, y, z = xi[:i].T
        line.set_data(x, y)
        line.set_3d_properties(z)

        pt.set_data(x[-1:], y[-1:])
        pt.set_3d_properties(z[-1:])

    ax.view_init(30, 0.09 * i)
    fig.canvas.draw()
    return lines + pts


# instantiate the animator.
anim = animation.FuncAnimation(fig, animate, init_func=init, \
                               frames=1000, interval=200, blit=True)

#HTML(anim.to_html5_video())
rc('animation', html='html5')
plt.close()
anim

At iteration k=   1 (time t=0.2000):
linear interpolation for t_past=-6.8000 requires at least two entries.
At iteration k=   1 (time t=0.2000):
linear interpolation for t_past=-6.8000 requires at least two entries.


Notice that two separate phase space points, initialized randomly, follow chaotic trajectories until a small perturbation is applied to the system. While the perturbation is "on", the two points settle onto two periodic orbits that were unstable previously. When the perturbation is turned off, the orbits become unstable once again, and the points resume their chaotic journey. 

## Notes:

Should you encounter difficulty in running the embedded animation, try to launch Jupter Notebook using the command:<br>
`jupyter notebook --NotebookApp.iopub_data_rate_limit=10000000000`

## References:

1) Gonzalez-Miranda, J.M. (2004). *Synchronization and Control of Chaos, An Introduction for Scientists and Engineers*. London, UK: Imperial College Press. <br>  
2) Parker, T.S. and Chua, L.O. (1989). *Practical Numerical Algorithms for Chaotic Systems*. New York, USA: Springer-Verlag. 